In [7]:
# general
import os
BASE_DIR = os.path.dirname(os.path.dirname(os.path.abspath('__file__')))

from pathlib import Path

# computation
import pandas as pd

# plotting
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import bokeh as bk
import bokeh.plotting as bp
from bokeh.models import tools as bmt, tickers
from bokeh.io import output_notebook, export_png

output_notebook()

Loading BokehJS ...

In [2]:
stations = [
    'Battambang', 'Chaktomuk', 'Kg._Thmar', 'Koh_Khel', 'Kompong_Cham', 'Kompong_Chen', 'Kompong_Kdei', 'Kompong_Thom',
    'Kratie', 'Lumphat', 'Neak_Luong', 'Phnom_Penh_Port', 'Prek_Kdam', 'Siempang', 'Sisophon', 'Stung_Treng', 'Voeun_Sai',
]

no_fit_stations = ['Phnom_Penh_Port', 'Prek_Kdam']

In [3]:
Path(f'{BASE_DIR}/spt_vs_mrc/').mkdir(parents=True, exist_ok=True)

dfs = []

for station in stations:
    obs = pd.read_csv(f'{BASE_DIR}/mrc_observations/{station}.csv')
    obs['datetime'] = pd.to_datetime(obs['datetime'])

    pred = pd.read_csv(f'{BASE_DIR}/spt_predictions/{station}.csv')
    pred['datetime'] = pd.to_datetime(obs['datetime'])

    obs = obs.rename(columns={'discharge': 'observation'})
    pred = pred.rename(columns={'discharge': 'prediction'})
    df = pd.merge(obs, pred, how='inner', on='datetime')
    df.sort_values(by=['datetime'], ascending=True, inplace=True)
    dfs.append({'station': station, 'df': df})

    df.to_csv(f'{BASE_DIR}/spt_vs_mrc/{station}.csv', encoding='utf-8', index=False)

In [12]:
Path(f'{BASE_DIR}/plot_exports/obs_vs_pred/').mkdir(parents=True, exist_ok=True)

for _df in dfs:
    station = _df['station']
    df = _df['df']

    # figure
    title = f'{station}: Observation Vs Prediction'
    x_axis_label = 'Datetime'
    y_axis_label = 'Discharge (m3/s)'

    # bokeh style
    TOOLS = 'pan,wheel_zoom,box_zoom,reset'
    hover_tool = bmt.HoverTool(
        tooltips=[
            ('date',      '$x{%F}'),
            ('discharge', '$y{0.00 a}'),
        ],
        formatters={
            '$x' : 'datetime',
        },
    )
#     TOOLTIPS = [
#         ('date',      '$x'),
#         ('discharge', '$y'),
#     ]
#     hover_tool = bmt.HoverTool(tooltips=TOOLTIPS)

    fig = bp.figure(title=title,
                    x_axis_label=x_axis_label,
                    y_axis_label=y_axis_label,
                    x_axis_type='datetime',
                    plot_height=300,
                    tools=TOOLS,
                   )
    fig.add_tools(hover_tool)
    fig.sizing_mode = 'scale_width'

#     fig.circle(datetime, observation, source=df, size=5)
    fig.line('datetime', 'observation', source=df, line_width=2, line_color='red', legend_label='observation')
    fig.line('datetime', 'prediction', source=df, line_width=2, line_color='blue', legend_label='prediction')
    fig.legend.location = 'top_left'
    fig.legend.click_policy = 'hide'

    try:
        bp.show(fig)
        export_png(fig, filename=f'{BASE_DIR}/plot_exports/obs_vs_pred/{station}.png')
    except Exception as e:
        print(f'station: {station} error')
        print(e)

    # plotly style
#     observation = go.Scattergl(x=df.datetime,
#                                y=df.observation,
#                                mode='lines+text',
#                                name = f'Observation',
#                                line=dict(color='red'),
#                                showlegend=True,
#                               )

#     prediction = go.Scattergl(x=df.datetime,
#                               y=df.prediction,
#                               mode='lines+text',
#                               name = f'Prediction',
#                               line=dict(color='blue'),
#                               showlegend=True,
#                              )


#     layout = go.Layout(title=title,
#                        xaxis=dict(title=x_axis_label),
#                        yaxis=dict(title=y_axis_label),
#                        showlegend=True)

#     fig = go.Figure(data=[observation, prediction], layout=layout)
#     fig.write_image(f'{BASE_DIR}/plot_exports/obs_vs_pred/{station}.png')
#     fig.show()